# Install và import các thư viện

In [5]:
!pip install emoji


In [1]:
import requests
from requests import session
import emoji
import json
s = session()
access_token = 'EAAD6V7os0gcBO44yJTr0fn3Xyi7idcS6mYdL23PHNwBTV7djOM65lIpZAawNGRs4frOq7tSZCzLTv0jjpfbP1wIbZAgnMO3eKNABcZCkmQOddAxWf0PvhAOVXZAClpiJ02Pk7CMB2OAfM1GIOJNiz6m4p8G2Ekcm40fTCbx3tM7xG9URp2huou10GBbWvyiaKqfrqu1F4twZDZD'
id_fanpage = '100067615970201'
name_fanpage = 'anhdavangvuive' # Fanpage: Anh Da Vàng
fields_feed = 'feed' # lấy tất cả các feed

# Phần crawl dữ liệu về các bài viết(chưa lấy dữ liệu về các user)

## Gọi api để lấy thông tin về các feed và lưu vào file feed_raw_data.json

In [7]:


raw_data_feed = s.get('https://graph.facebook.com/'+id_fanpage+'?fields='+fields_feed+'&access_token='+access_token) # có thể xem chi tiết về số lượng share, chi tiết comment, nội dung bài viết(message), thời gian đăng bài
#raw_data_feed.json()['feed']['data'][0]['created_time'][:10]\
#raw_data_feed.json()

In [8]:
#chạy lần đầu tiên lấy <= 25 feed đầu tiên cho vào list res_raw_json
count_feed = 0 # biến đếm số bài viết

res_raw_json = [] #list các feed (các feed ở dạng json)
for i in range(len(raw_data_feed.json()['feed']['data'])):
    count_feed += 1
    res_raw_json.append(raw_data_feed.json()['feed']['data'][i])
#chạy lần thứ 2 lấy <= 25 feed tiếp theo cho vào list res_raw_json    
mask_data_feed =  s.get(raw_data_feed.json()['feed']['paging']['next'])# gọi api đến next page (mỗi lần (default nếu không limit với giá trị limit có thể chạy từ 0 đến 250 bài) gọi chỉ lấy được 25 feed)  
for i in range(len(mask_data_feed.json()['data'])):
    count_feed += 1
    res_raw_json.append(mask_data_feed.json()['data'][i])
#tiếp tục chạy đến khi đủ 500 bài (page này đến thời điểm 3/11/2023 có hơn 5500 bài viết)
check_not_enough_feed = True # biến check đến khi đủ 500 bài 
while(check_not_enough_feed): 
    if('paging' in mask_data_feed.json()):
        mask_data_feed = s.get(mask_data_feed.json()['paging']['next'])
        if('data' in mask_data_feed.json()):
            for i in range(len(mask_data_feed.json()['data'])):
                count_feed += 1
                res_raw_json.append(mask_data_feed.json()['data'][i])
                if(count_feed >= 500):
                    check_not_enough_feed = False
                    break
with open('feed_raw_data.json', 'w') as feed_raw_data:
    json.dump(res_raw_json,feed_raw_data)
        

In [9]:
print(len(res_raw_json))

500


### Hàm làm sạch chuỗi nội dung bài viết

In [10]:
#hàm cleanString
def clean_string(st):
    e = emoji.emoji_list(emoji.emojize(st)) # lấy ra các emoji
    for i in e :
        st = st.replace(i['emoji'],'')      
    st =  st.replace("Cre:", '')    
    st =  st.replace("cre:", '')
    st =  st.replace("P/s:", '')
    st =  st.replace("p/s:", '')
    st =  st.replace("Cre :", '')
    st =  st.replace("cre :", '')
    st =  st.replace("cre", '')
    st =  st.replace("Cre", '')
    return st

### Hàm tách hastag ra khỏi nội dung bài viết

In [11]:
#hàm tách hastag:
def split_hastag(s):
    start = s.find('#')
    result = s[start:]
    end  = result.find(' ')
    if end == -1:
        end  = result[1:].find('#')
    if end == -1:
        end = result.find('\n')
    if end == -1:
        return result[1:]    
    result = result[:end + 1]
    subresult = result[1:]
    subresult.replace("\n",'')
    subresult = subresult.strip()
    return subresult


## Lấy các dữ liệu đã có trong file_raw_data.json và crawl tất cả các comments của từng bài viết

### lấy gần như tất cả dữ liệu cần thiết (chưa lấy tổng số comments và chi tiết về reactions )

In [12]:
#đọc file feed_raw_data để xử lí
raw_data_read = ''
with open('feed_raw_data.json','r') as handler:
    raw_data_read = json.load(handler)
#raw_data_read[0]['comments']['data'][0]['message_tags'][0]['id']    
comments_details_lists = [] #
list_message_post = [] #nội dung của các bài viết
list_time_created = [] #thời gian đăng bài 
hours_time_created = []#thời gian đăng bài theo giờ
shared_total = []#số lượng share 
source_picture = [] #list_link_picture
source_video = [] # list_link_video
comments_time_created = [] #list_time_created_comments
link_post = []#list_link_post
list_len_video =[]#list_len_of_video
list_hastag =[] # list_hastag 
for post in raw_data_read:
    comments_details_lists_per_post = []
    #lấy nội dung bài viết(thay icon bằng chuỗi 'icon)
    raw_message_post = post['message']
    clean_message_post = clean_string(raw_message_post)
    for i in range(clean_message_post.count('#')):
        list_hastag.append(split_hastag(clean_message_post))
        sub = '#'+split_hastag(clean_message_post)
        clean_message_post= clean_message_post.replace(sub,'')
    list_message_post.append(clean_message_post)
    #lấy thời gian đăng bài
    list_time_created.append(post['created_time'])
    hours_time_created.append(post['created_time'][11:13])
    #lấy độ dài video (nếu có)
    len_video = '0'
    if('properties' in post):
         for vid in post['properties']:
              if('text'in vid):
                   len_video = vid['text']
    list_len_video.append(len_video)
    #lấy comment (25 comment gần nhất)
    comments_details_lists_per_post = []
    for cm in range(len(post['comments']['data'])):
            comments_details =  post['comments']['data'][cm]['from'] # user comments
            comments_details['message'] =  clean_string(post['comments']['data'][cm]['message']) # message comments
            comments_details['time_created'] = post['comments']['data'][cm]['created_time'][11:13]#time comments
            comments_details['id_tag'] = '' # user_tag 
            if('message_tags' in  post['comments']['data'][cm]):
                comments_details['id_tag'] = post['comments']['data'][cm]['message_tags'][0]['id']
            comments_details_lists_per_post.append(comments_details)
    comments_details_lists.append(comments_details_lists_per_post)        
    # đoạn lấy tất cả comment này dùng hơi tốn clone fb và thường bị chặn ip khi spam lấy quá nhiều comment (của 500 bài viết)   
        #lấy comment lần 2
    link_next_comments_page =''    
    if('next' in post['comments']['paging']):
            link_next_comments_page = s.get(post['comments']['paging']['next'] )
            #lấy dữ liệu
            if('data' in link_next_comments_page.json()):
                for cmt_d in link_next_comments_page.json()['data']:
                    cmt_dt = cmt_d['from']
                    cmt_dt['message'] = clean_string(cmt_d['message'])
                    cmt_dt['time_created'] = cmt_d['created_time'][11:13]
                    cmt_dt['id_tag'] = ''
                    if('message_tags' in cmt_d):
                        cmt_dt['id_tag'] = cmt_d['message_tags'][0]['id']
                    comments_details_lists_per_post.append(cmt_dt) 
                comments_details_lists.append(comments_details_lists_per_post)    
                     
            #     
    if(link_next_comments_page!= '') :       #   
        if('paging' in link_next_comments_page.json()):
            while ('next' in link_next_comments_page.json()['paging']):
                    link_next_comments_page = s.get(link_next_comments_page.json()['paging']['next'] )
                    #lấy dữ liệu
                    if('data' in link_next_comments_page.json()):  
                        for cmt_d in link_next_comments_page.json()['data']:
                            cmt_dt = cmt_d['from']
                            cmt_dt['message'] = clean_string(cmt_d['message'])
                            cmt_dt['time_created'] = cmt_d['created_time'][11:13]#checkpoint
                            cmt_dt['id_tag'] = ''
                            if('message_tags' in cmt_d):
                                cmt_dt['id_tag'] = cmt_d['message_tags'][0]['id']
                            comments_details_lists_per_post.append(cmt_dt)  
                        comments_details_lists.append(comments_details_lists_per_post)     
                               
                    else:
                        break         
                    #
       
    #lấy số lượng share
    if('shares' in post):
        shared_total.append(post['shares']['count'])       
    else:
         shared_total.append(0)
    #lấy source picture
    if('picture' in post):
         source_picture.append(post['picture'])
    else:
         source_picture.append('')     
    #lấy source video
    if('source' in post):
         source_video.append(post['source'])
    else:
         source_video.append('')    
    #lấy link post
    link = 'facebook.com/'+post['id']       
    link_post.append(link)     

# list_message_post
# list_time_created
# hours_time_created 
# comments_details_lists
# shared_total

### Lưu các dữ liệu vào file tương ứng

In [13]:
#lưu list_hastag vào file_hastag.txt
with open('file_hastag.txt','w',encoding='utf8') as handler:
    for i in list_hastag:
        handler.write(i)
        handler.write("\n")

In [14]:
#lưu list_len_video vào file_len_video
with open('file_len_video.txt','w') as handler:
    for i in list_len_video:
        handler.write(i)
        handler.write("\n")

In [15]:
#lưu source_picture vào file file_source_picture
with open("file_source_picture",'w') as handler:
    for i in source_picture:
        handler.write(i)
        handler.write("\n")

In [16]:
#lưu source_video vào file file_source_video
with open("file_source_video",'w') as handler:
    for i in source_video:
        handler.write(i)
        handler.write("\n")

In [17]:
#lưu link_post vào file link_post.txt
with open("link_post.txt", 'w') as handler:
    for i in link_post:
        handler.write(i)
        handler.write("\n")

In [18]:
#lưu thời gian đăng bài theo giờ vào file hours_created.txt
with open("hours_created",'w') as handler:
    for i in hours_time_created:
        handler.write(i)
        handler.write("\n")

In [19]:
#lưu thời gian đăng bài vào file time_created.txt
with open("time_created", 'w') as handler:
    for i in list_time_created:
        handler.write(i)
        handler.write("\n")

In [20]:
#lưu nội dung bài viết vào file raw_message.txt
with open('raw_message.txt','w',encoding='utf8') as handler:
    for i in list_message_post:
        handler.write(i)
        handler.write("\n")
        handler.write("\n")

In [21]:
#lưu comments_details_lists vào file raw_comments.json
with open('raw_comments.json','w') as file_raw_comments:
    json.dump(comments_details_lists,file_raw_comments)


In [22]:
#lưu shared_total vào file_shared_total.txt
with open("file_shared_total.txt",'w') as handler:
    for i in shared_total:
        handler.write(str(i))
        handler.write("\n")

### Gọi api để lấy chi tiết reactions của bài viết lưu bài viết vào file_raw_data_reactions.json

In [23]:
# lấy chi tiết từng reaction của 1 bài viết" LIKE, LOVE, WOW, HAHA, SAD, ANGRY, THANKFUL, PRIDE, CARE, FIRE, HUNDRED"
'100067615970201/feed?fields=reactions.type(LOVE).limit(0).summary(total_count).as(reactions_love),reactions.type(WOW).limit(0).summary(total_count).as(reactions_wow)'
raw_data_reaction = []
count_data_reactions = 0
fields_reactions_details = 'feed{reactions.type(LIKE).limit(0).summary(total_count).as(reactions_like),reactions.type(LOVE).limit(0).summary(total_count).as(reactions_love),reactions.type(WOW).limit(0).summary(total_count).as(reactions_wow),reactions.type(HAHA).limit(0).summary(total_count).as(reactions_haha),reactions.type(SAD).limit(0).summary(total_count).as(reactions_sad),reactions.type(ANGRY).limit(0).summary(total_count).as(reactions_angry)}' 
#chạy lần đầu tiên
raw_data_reaction_details = s.get('https://graph.facebook.com//v18.0/'+id_fanpage+'?fields='+fields_reactions_details+'&access_token='+access_token)
for i in raw_data_reaction_details.json()['feed']['data']:
    raw_data_reaction.append(i)
    count_data_reactions += 1
#

In [24]:
#chạy lần 2
next_page_reactions_details = ''
if('paging' in raw_data_reaction_details.json()['feed']):
    if('next' in raw_data_reaction_details.json()['feed']['paging']):
        next_page_reactions_details =  s.get(raw_data_reaction_details.json()['feed']['paging']['next'])
        #lấy reactions
        if('data' in next_page_reactions_details.json()):
            for i in next_page_reactions_details.json()["data"]:
                raw_data_reaction.append(i)
                count_data_reactions+=1
        #        
#                

In [25]:
#chạy để lấy tất cả reactions của 500 bài viết
check_not_enough_reactions = True
while('paging' in next_page_reactions_details.json() and check_not_enough_reactions):
    if('next' in next_page_reactions_details.json()['paging']):
        next_page_reactions_details =  s.get(raw_data_reaction_details.json()['feed']['paging']['next'])
        #lấy reactions
        if('data' in next_page_reactions_details.json()):
            for i in next_page_reactions_details.json()["data"]:
                raw_data_reaction.append(i)
                count_data_reactions+=1
                if count_data_reactions == 500 :
                    check_not_enough_reactions = False
                    break
        #          

- Lưu dữ liệu reactions vừa lấy được vào file.json tương ứng

In [26]:
#lưu raw_data_reaction vào file_raw_data_reactions.json
with open("file_raw_data_reactions.json",'w') as handler:
    json.dump(raw_data_reaction, handler)

In [27]:
total_reactions = []
#lấy tổng số reactions của từng bài viết
for j in range(len(raw_data_reaction)):
    total = 0
    for i in raw_data_reaction[j]:
        if('summary' in raw_data_reaction[j][i]):
            total += raw_data_reaction[j][i]['summary']['total_count']
    total_reactions.append(total)
        

In [28]:
#lưu total reactions vào file 
with open("file_total_reactions.txt",'w') as handler:
    for i in total_reactions:
        handler.write(str(i))
        handler.write("\n")

      

In [29]:
# list_message_post
# list_time_created
# hours_time_created 
# total_reactions
# shared_total
# comments_details_lists
# user_id

### Gọi api lấy chi tiết tổng số comments của từng bài viết và lưu vào file tương ứng

In [30]:
# lấy total comments của bài viết
fields_total_comments = 'feed{comments.summary(true)}'
count_total_feed_comments = 0
total_comments = []
#lần
raw_total_comments = s.get('https://graph.facebook.com/' + id_fanpage + '?' + 'fields=' + fields_total_comments+'&access_token='+access_token)
for i in range(len(raw_total_comments.json()['feed']['data'])):
    total_comments.append(raw_total_comments.json()['feed']['data'][i]['comments']['summary']['total_count'])
    count_total_feed_comments += 1
#lần 2
next_raw_total_comments = ''
if('paging' in raw_total_comments.json()['feed']):
    if('next' in raw_total_comments.json()['feed']['paging']):
        next_raw_total_comments= s.get(raw_total_comments.json()['feed']['paging']['next'])
        for i in range(len(next_raw_total_comments.json()['data'])):
            total_comments.append(next_raw_total_comments.json()['data'][i]['comments']['summary']['total_count'])  
            count_total_feed_comments += 1  
#lấy tiếp  
check_not_enough_feed_comments = True
while(check_not_enough_feed_comments):
    if('paging' in next_raw_total_comments.json()):
        if('next' in next_raw_total_comments.json()['paging']):
            next_raw_total_comments= s.get(next_raw_total_comments.json()['paging']['next'])
            for i in range(len(next_raw_total_comments.json()['data'])):
                total_comments.append(next_raw_total_comments.json()['data'][i]['comments']['summary']['total_count'])  
                count_total_feed_comments += 1  
                if(count_total_feed_comments == 500):
                    check_not_enough_feed_comments = False
                    break            


In [31]:
# lưu tổng số comments của từng bài viết  vào file
with open('total_comments.txt','w') as handler:
    for i in total_comments:
        handler.write(str(i))
        handler.write("\n")
                        

In [32]:
# list_message_post
# list_time_created
# hours_time_created 
# total_comments
# total_reactions
# raw_data_reaction
# shared_total
# comments_details_lists
# user_id
# source picture
# source video

### Lấy chi tiết các reactions dựa trên file_raw_data_reaction vừa lấy được ở trên

In [33]:
total_reactions_like = []
total_reactions_love = []
total_reactions_wow = []
total_reactions_haha = []
total_reactions_sad = []
total_reactions_angry = []
for i in raw_data_reaction:
    
    total_reactions_like.append(i['reactions_like']['summary']['total_count'])
    total_reactions_love.append(i['reactions_love']['summary']['total_count'])
    total_reactions_wow.append(i['reactions_wow']['summary']['total_count'])
    total_reactions_haha.append(i['reactions_haha']['summary']['total_count'])
    total_reactions_sad.append(i['reactions_sad']['summary']['total_count'])
    total_reactions_angry.append(i['reactions_angry']['summary']['total_count'])

## Xử lí lấy id của user_comments và id của user được tag

### chuẩn bị dữ liệu

In [34]:
#lấy tất cả các user id của bình luận cho vào set (không trùng lặp người bình luận)
user_id_comment_set =  set()
user_id_comment_list = []
user_id_tag_list = []
for i in comments_details_lists:
    for j in i:
        user_id_comment_set.add(j['id'])
        user_id_comment_list.append(j['id'])
        if(j['id_tag'] != ''):
            user_id_tag_list.append(j['id_tag'])
#lấy tất cả user id của bình luận (có tính trùng lặp)
#lấy tất cả id_tag (id người được tag trong bình luận)

In [35]:
print(len(user_id_comment_list))
print(len(user_id_comment_set))
print(len(user_id_tag_list))
#hơn 1 nửa số comments là có tag nhau 

1947335
21293
1396365


### Lưu dữ liệu

In [36]:
#lưu user_id_comment_set vào trong file.txt
with open('file_user_id_comment_set.txt', 'w') as handler:
    for i in user_id_comment_set:
        handler.write(str(i))
        handler.write("\n")
#lưu user_id_comment_list vào file.txt
with open('file_user_id_comment_list.txt', 'w') as handler:
    for i in user_id_comment_list:
        handler.write(str(i))
        handler.write("\n")
#lưu user_id_tag_list vào file.txt
with open('file_user_id_tag_list.txt', 'w') as handler:
    for i in user_id_tag_list:
        handler.write(str(i))
        handler.write("\n")        

## Tổng hợp lại tất cả dữ liệu vừa thu thập được lưu vào file csv

- Tổ chức lại toàn bộ bộ dữ liệu vào dict

In [37]:

big_table = {'message_post' : list_message_post, 'id_post' : link_post,'time_created_total' : list_time_created, 'time_created_hours' : hours_time_created, 
                          'total_of_comments' : total_comments, 'total_of_reactions' : total_reactions, 'reactions_like' : total_reactions_like,'reactions_love' : total_reactions_love,
                          'reactions_wow' : total_reactions_wow, 'reactions_haha' : total_reactions_haha, 'reactions_sad' : total_reactions_sad, 'reactions_angry' : total_reactions_angry,
                          'total_of_share':shared_total, 'comments_details' : comments_details_lists, 'source_of_picture': source_picture, 
                          'source_of_video' : source_video, 'len_video' : list_len_video}


- Chuẩn bị dữ liệu để lưu vào file csv

In [38]:
data_table = []
for i in range(500):
    data_table.append({'message_post': big_table['message_post'][i], 'id_post': big_table['id_post'][i], 'time_created' : big_table['time_created_total'][i],
                       'hours_time_created' : big_table['time_created_hours'][i], 'total_comments': big_table['total_of_comments'][i],
                       'total_of_reactions': big_table['total_of_reactions'][i],
                       'reactions_like': big_table['reactions_like'][i], 'reactions_love': big_table['reactions_love'][i],
                       'reactions_wow': big_table['reactions_wow'][i],
                       'reactions_haha': big_table['reactions_haha'][i],
                       'reactions_sad': big_table['reactions_sad'][i],
                       'reactions_angry': big_table['reactions_angry'][i],'total_share': big_table['total_of_share'][i],
                       'comments_details' : big_table['comments_details'][i], 'source_picture' : big_table['source_of_picture'][i],
                       'source_video': big_table['source_of_video'][i],
                       'len_video': big_table['len_video'][i]
                       })

In [39]:
header = ['message_post','id_post', 'time_created', 'hours_time_created', 'total_comments', 'total_of_reactions', 'reactions_like', 'reactions_love', 'reactions_wow'
          , 'reactions_haha',  "reactions_sad",  'reactions_angry', 'total_share', 'comments_details',
          'source_picture', 'source_video', 'len_video']

- Lưu dữ liệu vào file csv

In [40]:
import csv
with open('data.csv','w', encoding='utf8') as handler:
    writer = csv.DictWriter(handler, fieldnames = header)
    writer.writeheader()
    writer.writerows(data_table)

# Crawl dữ liệu về các user

## Xử lí dữ liệu của các id user để crawl

- Kiểm tra các id của user

In [41]:
for i in user_id_comment_set:
    print(i)

100048894999974
1307607897
100069682896950
100046252582084
100009530645744
100016939515001
100043666877643
100007901682267
100009858461500
100030758292032
100026138650790
100061089681206
100027031056168
100009443071447
100010660935001
100004122369089
100004622980691
100062384422908
100009421197576
100052774443670
1315347905
100018034364190
100001074686726
100017658397159
100028572726415
100093020285559
100014889228520
100065491852127
100065369765846
100025121331844
100066792176747
100000357812874
100081426878694
100013079144998
100050790347313
100008047985577
100060318888769
100077386486576
100000185150462
100005738289607
100009565055492
100004204357246
100006138403493
100022850539628
100003796344768
100012861303935
100075988368451
100052087840782
100079671574751
100010376358285
100013377763932
100083853807574
100008136131637
100071016211219
100014822978612
100038964844558
100028190181231
100002496233164
100005688824041
100072061654123
100071929470968
100089122747560
100051947951651
10

- Lấy các id của user từ file đã lưu

In [16]:
user_id_comment_set_1 = []
with open('file_user_id_comment_set.txt','r')as handler:
    user_id_comment_set_1 = handler.readlines()

In [17]:
user_id_comment_set_1

['100048894999974\n',
 '1307607897\n',
 '100069682896950\n',
 '100046252582084\n',
 '100009530645744\n',
 '100016939515001\n',
 '100043666877643\n',
 '100007901682267\n',
 '100009858461500\n',
 '100030758292032\n',
 '100026138650790\n',
 '100061089681206\n',
 '100027031056168\n',
 '100009443071447\n',
 '100010660935001\n',
 '100004122369089\n',
 '100004622980691\n',
 '100062384422908\n',
 '100009421197576\n',
 '100052774443670\n',
 '1315347905\n',
 '100018034364190\n',
 '100001074686726\n',
 '100017658397159\n',
 '100028572726415\n',
 '100093020285559\n',
 '100014889228520\n',
 '100065491852127\n',
 '100065369765846\n',
 '100025121331844\n',
 '100066792176747\n',
 '100000357812874\n',
 '100081426878694\n',
 '100013079144998\n',
 '100050790347313\n',
 '100008047985577\n',
 '100060318888769\n',
 '100077386486576\n',
 '100000185150462\n',
 '100005738289607\n',
 '100009565055492\n',
 '100004204357246\n',
 '100006138403493\n',
 '100022850539628\n',
 '100003796344768\n',
 '100012861303935\n'

- Xử lí các kí tự thừa ở từng id

In [18]:
for i in range(len(user_id_comment_set_1)):
    user_id_comment_set_1[i] = user_id_comment_set_1[i][:user_id_comment_set_1[i].find("\n")]

In [19]:
for i in user_id_comment_set_1:
    print(i)

100048894999974
1307607897
100069682896950
100046252582084
100009530645744
100016939515001
100043666877643
100007901682267
100009858461500
100030758292032
100026138650790
100061089681206
100027031056168
100009443071447
100010660935001
100004122369089
100004622980691
100062384422908
100009421197576
100052774443670
1315347905
100018034364190
100001074686726
100017658397159
100028572726415
100093020285559
100014889228520
100065491852127
100065369765846
100025121331844
100066792176747
100000357812874
100081426878694
100013079144998
100050790347313
100008047985577
100060318888769
100077386486576
100000185150462
100005738289607
100009565055492
100004204357246
100006138403493
100022850539628
100003796344768
100012861303935
100075988368451
100052087840782
100079671574751
100010376358285
100013377763932
100083853807574
100008136131637
100071016211219
100014822978612
100038964844558
100028190181231
100002496233164
100005688824041
100072061654123
100071929470968
100089122747560
100051947951651
10

## Bắt đầu crawl dữ liệu của user

- Thực hiện lấy tất cả thông tin về user 

In [30]:
#shell này chạy mất hơn 1h30p (gần 100 phút), lấy tát cả thông tin về user bình luận
fields_user_data = 'birthday,education,gender,hometown,first_name,middle_name'#checkpoint
list_data_user = []
list_token = ['EAABwzLixnjYBO0HHXrkuzQgmF2b51xwySXEyZAOqZAm1kZAA7RmhoZAG9OgPMSgEyfOfZBwRs6YeFZCL1nQ4MIetg6K4SWLwiHjsj4tXL3bZCILCZCF2EFkmktI7VpcpZB9dSD3El8kfZAqzLprkfy8AqYgasppFRHL7jP2xn3YGeMpZA0VfjZC5XXORVkC4wraI7LEdZAfoZD',
              'EAABwzLixnjYBO8qVZAFbXDVw2xUDS8Imxan0pGvuBiYIUAHAj6zKKRT8iWsNhaZAvq79HUY9xN3jzEz5ZAtymj62YGHk8VZAaKFeFgGnhd5lEwB8R7ZBpupJBWL7kM18G8PIpQrZCQK25hpyCJZAxYFdylZCwUP8S5XPJPOuJRc4UjyXeCMr8A4UFlS5v5vybjTAOIzVqKpeK6ZBRQVmghQ3CYu0ZD',
              'EAABwzLixnjYBOyP0HMaICyc8LGCLadNgNqkzKlH8GSz9ny6VtMdBUofWzcZBIcV37ooJfzE7P1GopdoxZAGk9ge8HbZBpiXCsUmLZCZBwMV6Sihy7tF3vUlKnTZBH4m02EtVU7mS54tuwpZBbHQ3z4QngWO6gwwqesITTyWRTTO5N1TOOskYkSM5Q50X9TQcy20ZBXKJfZA8ZD',
              'EAABwzLixnjYBOZCh3wvZAZCbGZCkaym05855ZBTBjJiOjJHc6C2ZCOVRdZBfIJi4MrQc4yr61uaaSOun9vWmq0YslfbpCIl0s9HH3pDuBxdXzZB08JzNITI9bZAQiIW9ZA363SBq8MzfcVqwblIRosRZCBxrEtvwN3Nm1hGkzqL2N05elnS1onviBC6wYTafNFB3URN5q2BugAZD',
              'EAABwzLixnjYBOZBBggaV0YD0xntjhSAw9xdHaovKQtaapgtITtbtv5eiVuBxQPSqvUhyWWsHACGAEZCZAmO2X0u1rDELoVwk4RWmb9dQR0pa258WUbSBCoUpoCqLBijUEuYi1MkNQyeDqXufPpUeRzTBHZCFKsxkY2ys4xZCGZB8VFQPnoAsZAGBsijETmGYY2pFh1AAWWqqlTrrZBMSXP0CyK0ZD',
              'EAABwzLixnjYBOZB5p2vW1KZC0pUzHBCNQYjmQj6XmnrimDnbLrPkDVjwZAGZCfZAp1AVCJEe16nOvXL2NZBSZA1Yq7vR2Frmi5cZCPqcykwa2DTeB4oSd6DxWhkCGXRGw4iP4pUKBwx15kirjO38NZBaKWoO5R5hEW3dy5n60dJZAj602nZBRbMqJewLcZCqmPJt8OOlWKLwmafGbWZA4xOwZD',
              'EAABwzLixnjYBOwTeqWalcPwYXX9iZA7tlFVYOifRujIbgUrW4u7aUV0SHN2vEDsZAF7pTPnrKQ66t66OL8ZBgZCuGZBT4BvE4mELlQas9TwYdaL0KaGhtbz5bKkSPtOdrKoTemf84OzEFcBf3L4crZAGx4tFcU7iRgLZAbCHjJTSe8Aoqtci5SEyNHpX0KaZBJYdcTPUxqd2zr9PZCEoZD'#error 368,
              'EAABwzLixnjYBOZB1wVwxWXOR9BFnPnZBtEjdVQ0MCOXRi0u2uqE51KxlZCoCj8wZB5IKm7ikOxK10yTlacAWGaFfDcbcC9mqfkJM8TOTGm9vfat8d6TCfNJ6J6YR3yLnO8bieYZAZBk31RZAkNHVzogyzEXrx4xbXQexoLk4d47ZBwOQx3oNvtRujm4fDQgzdui0UHurXOZCOYjXEkIM1AW0ZD'#error 190,
               'EAABwzLixnjYBOZBCp2i05RCHLkUyb8K3fqZBDWAp3y3wCWnAOPQtKwilN414htZA1LnnBKf8wVDoZAiXqdjJFrYBsnZBQjUKoqYhdzmfPGRm8BkGit77ymbADTJ9q8pkixLJGM0J3GTgTQuIjsEyzZBqZB8OfhqtXywtVutLwU71LsV4OwzjP8c9DN1kqxXJfyJqSwZD',
               'EAABwzLixnjYBO2e93D1BPUan2VRvhZCSgi2ZATDcUWgm1tyuOQMNiRvhRDxIohy1iqvyvQDMNUerjXsuVJydxHUereLDrqAr2rjgZC5ZA2BCClo8eRHmfxWIZBafcjew5Sqxi8LiYOfICG8oXGmCot0ka5zzRlGqQLIrFdexzH4gfm3uf2yqqktqhRISkaG98lVoZD'
              ]
ind = 0
for i in user_id_comment_set_1:
     user_data = s.get('https://graph.facebook.com/'+i+'?fields='+fields_user_data+'&access_token='+list_token[ind])
     if('error' in user_data.json()):
          if 'code' in user_data.json()['error']:
               if( ind < 9 ):
                    if ((user_data.json()['error']['code'] == 368 or  user_data.json()['error']['code'] == 190)):
                         
                              ind += 1
                              user_data = s.get('https://graph.facebook.com/'+i+'?fields='+fields_user_data+'&access_token='+list_token[ind])
               else:
                    break           
     print(ind)
     list_data_user.append(user_data.json())
     print(user_data.json())

0
{'birthday': '11/05', 'gender': 'male', 'first_name': 'Đăng', 'id': '100048894999974'}
0
{'education': [{'concentration': [{'id': '135271467301263', 'name': 'Kế Toán'}], 'school': {'id': '103074693133977', 'name': 'Vinh University'}, 'type': 'College', 'id': '2099601572112'}, {'school': {'id': '118657508177991', 'name': 'DH Vinh'}, 'type': 'College', 'id': '2440328930083'}, {'school': {'id': '112930372119479', 'name': 'THPT Lê Lợi'}, 'type': 'High School', 'year': {'id': '399262097214547', 'name': '2005'}, 'id': '2099576291480'}, {'classes': [{'id': '149280891799043', 'name': 'A2 (2005 - 2008)'}], 'school': {'id': '175858972472220', 'name': 'lê lợi'}, 'type': 'High School', 'id': '1670338320799'}, {'school': {'id': '110199595676757', 'name': 'PTTH Lê Lợi'}, 'type': 'High School', 'id': '2440328810080'}], 'gender': 'male', 'first_name': 'Tiến', 'middle_name': 'Văn', 'id': '1307607897'}
0
{'education': [{'school': {'id': '110086407934675', 'name': 'Trường Cao Đẳng Y Tế Trà Vinh'}, 'typ

In [31]:
len(list_data_user)

21293

## Lưu data về user vừa lây vào file json tương ứng

In [34]:
#cho list_data_user vao file user_data_js.json    
with open('user_data_js.json','w') as handler:
    json.dump(list_data_user,handler)  
